# Estimation de la latence et de la capacité d’une connexion à partir de mesures asymétriques

Ce document correspond au Sujet 4 du module 3 du MOOC "Recherche reproductible : principes méthodologiques pour une science transparente".

On s'intéresse à comparer un modèle simple de la performance d'une connexion de réseau avec des données réelles.

In [19]:
import os
from os.path import exists
import requests
import gzip

In [20]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd

## Téléchargement des données

On s'intéresse à deux jeux de données hébergés en ligne. La première étape est de les télécharger en local.

In [42]:
# Noms des fichiers en local
filenames = [
    "liglab2.log", 
    "stackoverflow.log",
]
# Adresse où les fichiers sont hébergés
urls = [
    "http://mescal.imag.fr/membres/arnaud.legrand/teaching/2014/RICM4_EP_ping/liglab2.log.gz",
    "http://mescal.imag.fr/membres/arnaud.legrand/teaching/2014/RICM4_EP_ping/stackoverflow.log.gz",
]

In [44]:
# Si les fichiers n'existent pas encore, on les télécharge.

def download_archive(filename, url):
    if not exists(filename):
        # On utilise le module requests pour récupérer les données en ligne
        archive = requests.get(url)
        # Le fichier est une archive .gz, on l'extrait avec le module gzip
        content = gzip.decompress(archive.content)
        
        open(filename,'wb').write(content)
        print(f"Téléchargement de {url} et extraction vers {filename}.")
    else:
        print(f"Le fichier {filename} existe déjà, pas besoin de le télécharger.")


for filename, url in zip(filenames, urls):
    download_archive(filename, url)


Le fichier liglab2.log existe déjà, pas besoin de le télécharger.
Le fichier stackoverflow.log existe déjà, pas besoin de le télécharger.


## Lecture des données
On extrait maintenant les données de l'outil `ping` sous forme d'un tableau `pandas`.

Le format étant relativement simple, il est possible de le faire en utilisant uniquement les fonctions de base des chaînes de caractères de Python.

Chaque ligne a la forme suivante:
```
[1421761682.052172] 665 bytes from lig-publig.imag.fr (129.88.11.7): icmp_seq=1 ttl=60 time=22.5 ms
```
On extrait uniquement les données qui nous intéressent :

 * la date de mesure (en secondes depuis le 1er janvier 1970) du 2e au 18e caractère
 * la taille du message (en octets), qui est suivi de la sous-chaîne `" bytes"`
 * la durée de réponse (en millisecondes), qui est précédé de `"time="` et suivi de `" ms"`

In [59]:
def extract_data(filename):
    timestamps = []
    msgsizes = []
    times = []
    err_count = 0
    success_count = 0
    
    with open(filename, 'r') as file:
        for line in file.readlines():
            try:
                # Date de mesure (timestamp)
                # du caractère n°1 au n°17 inclus (numérotés à partir de 0)
                ts_str = line[1:18]
                ts_float = float(ts_str)
                # On convertit en date pandas
                ts = pd.Timestamp(ts_float, unit='s')

                # Taille du message (message size)
                ms_str = line[20:line.index(" bytes")]
                ms_int = int(ms_str)

                # Durée de l'échange (time)
                time_str = line[line.index('time=')+5:line.rindex(" ms")]
                time_float = float(time_str)
                
                # Une fois les valeurs trouvées, on les ajoute au tableau
                timestamps.append(ts)
                msgsizes.append(ms_int)
                times.append(time_float)
                success_count += 1
                
            except ValueError:
                # Lorsqu'il manque l'une des valeurs, on oublie la ligne correspondante
                err_count += 1
           
    total_count = success_count + err_count
    print(f"{success_count} lignes lues avec succès ({100*err_count/total_count:.2f}% d'échecs)")
    return pd.DataFrame({"timestamp":timestamps, "msgsize":msgsizes, "time":times})
    

extract_data(filenames[0])

44036 lignes lues avec succès, (0.85% d'échecs)


msgsize   time                  timestamp
0          665  22.50 2015-01-20 13:48:02.052172
1         1373  21.20 2015-01-20 13:48:02.277315
2          262  21.20 2015-01-20 13:48:02.502054
3         1107  23.30 2015-01-20 13:48:02.729257
4         1128   1.41 2015-01-20 13:48:02.934648
5          489  21.90 2015-01-20 13:48:03.160397
6         1759  78.70 2015-01-20 13:48:03.443055
7         1146  25.10 2015-01-20 13:48:03.672157
8          884  24.00 2015-01-20 13:48:03.899933
9         1422  19.50 2015-01-20 13:48:04.122687
10        1180  18.00 2015-01-20 13:48:04.344135
11         999  18.80 2015-01-20 13:48:04.566271
12        1020  24.30 2015-01-20 13:48:04.998504
13          71   3.45 2015-01-20 13:48:05.205172
14          34   5.85 2015-01-20 13:48:05.414106
15        1843   2.31 2015-01-20 13:48:05.620117
16         407   1.14 2015-01-20 13:48:05.824949
17         356   1.10 2015-01-20 13:48:06.029177
18        1511   2.18 2015-01-20 13:48:06.234464
19         587   1.27 2015-01-20 13:48:06.438772
20         809   1.33 2015-01-20 13:48:06.643208
21        1364   1.51 2015-01-20 13:48:06.848323
22        1153   1.44 2015-01-20 13:48:07.053400
23         853   1.30 2015-01-20 13:48:07.257704
24        1510   2.17 2015-01-20 13:48:07.463275
25         123   1.21 2015-01-20 13:48:07.668423
26        1966   2.20 2015-01-20 13:48:07.874230
27         933   1.34 2015-01-20 13:48:08.078667
28         922   1.42 2015-01-20 13:48:08.283655
29          24   1.12 2015-01-20 13:48:08.488688
...        ...    ...                        ...
44006     1772  28.80 2015-01-20 16:26:20.743715
44007       41   1.14 2015-01-20 16:26:20.949053
44008     1944   2.32 2015-01-20 16:26:21.155685
44009      400   1.98 2015-01-20 16:26:21.362095
44010      226   3.01 2015-01-20 16:26:21.569409
44011      466   7.45 2015-01-20 16:26:21.780805
44012      350  13.50 2015-01-20 16:26:21.998869
44013     1829  45.90 2015-01-20 16:26:22.248969
44014     1954  58.50 2015-01-20 16:26:22.512386
44015     1074   1.45 2015-01-20 16:26:22.717961
44016       46   1.11 2015-01-20 16:26:22.923292
44017     1844   2.26 2015-01-20 16:26:23.129965
44018      645   1.24 2015-01-20 16:26:23.335449
44019      444   1.25 2015-01-20 16:26:23.540901
44020     1940   2.46 2015-01-20 16:26:23.747983
44021     1411   1.47 2015-01-20 16:26:23.954099
44022       49   1.21 2015-01-20 16:26:24.159879
44023      420   1.55 2015-01-20 16:26:24.365815
44024      227   1.22 2015-01-20 16:26:24.571516
44025      947   1.34 2015-01-20 16:26:24.777325
44026     1960   2.43 2015-01-20 16:26:24.983905
44027      531   1.19 2015-01-20 16:26:25.188976
44028      374   1.14 2015-01-20 16:26:25.394275
44029     1503   2.19 2015-01-20 16:26:25.600745
44030      572   1.29 2015-01-20 16:26:25.805877
44031     1338   1.47 2015-01-20 16:26:26.011910
44032     1515   7.02 2015-01-20 16:26:26.222729
44033     1875   2.33 2015-01-20 16:26:26.429007
44034     1006   1.61 2015-01-20 16:26:26.634747
44035     1273   1.35 2015-01-20 16:26:26.840222

[44036 rows x 3 columns]